In [1]:
%pip install transformers
%pip install datasets
%pip install sentencepiece
%pip install pandas openpyxl

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd

# Specify the file path
file_path = '/project/home/p_babro/p_babel/v4_slant/pooled_v4_xlmRoberta_training.xlsx'

# Read the Excel file
df = pd.read_excel(file_path)

# Display the DataFrame
print(df.head())

   labels                                               text
0       1  Strach z osobního selhání často v kritických o...
1       5              Pre týchto ľudí treba nájsť riešenie.
2       5  Čestnými hosty byli bývalý spolkový prezident ...
3       4           Vaše milá slova mi opravdu zlepšila den.
4       4         Ďakujem mnohokrát! Z pochvaly máme radosť.


In [6]:
# Load data from Excel file
df = pd.read_excel(file_path)

# Print the column names to verify
print(df.columns)


Index(['labels', 'text'], dtype='object')


In [3]:
from transformers import XLMRobertaTokenizer, XLMRobertaForSequenceClassification

# Model and tokenizer initialization
tokenizer = XLMRobertaTokenizer.from_pretrained('xlm-roberta-base')
model = XLMRobertaForSequenceClassification.from_pretrained('xlm-roberta-base')

Some weights of XLMRobertaForSequenceClassification were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [9]:
def start_train(df, model_name, batch_size, lr, max_length, num_epochs):

    # Prepare labels
    label_encoder = LabelEncoder()
    labels = df[label_column]
    labels = label_encoder.fit_transform(labels)
    num_labels = len(set(labels))

    # Hugging Face Datasets format
    train_dataset = Dataset.from_pandas(train_data)
    val_dataset = Dataset.from_pandas(val_data)
    test_dataset = Dataset.from_pandas(test_data)

    # Load tokenizer
    tokenizer = AutoTokenizer.from_pretrained(model_name)

    # Tokenize
    train_dataset = train_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=train_dataset.column_names)
    val_dataset = val_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=val_dataset.column_names)
    test_dataset = test_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=test_dataset.column_names)

    # Load model
    model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=num_labels, problem_type="multi_label_classification")

    # Training arguments
    training_args = TrainingArguments(
        output_dir=drive_folder_to_save,
        logging_dir=drive_folder_to_save,
        logging_strategy='epoch',
        logging_steps=100,
        num_train_epochs=num_epochs,
        per_device_train_batch_size=batch_size,
        per_device_eval_batch_size=batch_size,
        learning_rate=lr,
        seed=42,
        save_strategy='epoch',
        save_steps=100,
        evaluation_strategy='epoch',
        eval_steps=100,
        save_total_limit=1,
        load_best_model_at_end=True,
    )

    # Create trainer
    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        compute_metrics=compute_metrics,
        callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
    )

    # Train model
    trainer.train()

    # Evaluate results
    predictions = trainer.predict(test_dataset).predictions
    preds = np.argmax(predictions, axis=1)
    accuracy = accuracy_score(test_data[label_column], preds)
    print(f'Accuracy: {accuracy}')
    precision, recall, f1, _ = precision_recall_fscore_support(test_data[label_column], preds, average='weighted')
    print(f'Accuracy: {accuracy}')
    print(f'Precision: {precision}')
    print(f'Recall: {recall}')
    print(f'F1 Score: {f1}')

    # Save model
    trainer.save_model(folder_to_save)


In [7]:
# Install necessary libraries
%pip install pandas openpyxl transformers datasets evaluate scikit-learn

# Import necessary libraries
import pandas as pd
import numpy as np
import torch
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from transformers import (XLMRobertaTokenizer, XLMRobertaForSequenceClassification, AutoTokenizer,
                          AutoModelForSequenceClassification, Trainer, TrainingArguments)
from datasets import Dataset
from transformers.trainer_callback import EarlyStoppingCallback
import evaluate
from typing import List, Tuple

# Define paths and columns
file_path = '/project/home/p_babro/p_babel/v4_slant/pooled_v4_xlmRoberta_training.xlsx'
text_column = 'text'  # Replace with your actual text column name
label_column = 'labels'  # Replace with your actual label column name
drive_folder_to_save = '/project/home/p_babro/p_babel/v4_slant'  # Replace with your actual save folder path

# Define functions
def load_data_from_excel(df, text_column: str, label_column: str) -> Tuple[List, List]:
    return df[text_column].tolist(), df[label_column].tolist()

def tokenize_dataset(data, tokenizer, max_length, num_labels):
    tokenized = tokenizer(data[text_column],
                          max_length=max_length,
                          truncation=True,
                          padding="max_length")

    labels = [x for x in data[label_column]]
    labels_tensor = torch.as_tensor(labels)
    labels_binary = torch.nn.functional.one_hot(labels_tensor, num_classes=num_labels).float()

    tokenized['labels'] = labels_binary

    return tokenized

def compute_metrics(eval_pred):
    metric = evaluate.load("accuracy")
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=1)
    reference_labels = [np.argmax(label) for label in labels]
    precision, recall, f1, _ = precision_recall_fscore_support(reference_labels, predictions, average='weighted')
    accuracy = accuracy_score(reference_labels, predictions)
    return {
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'f1': f1
    }

# Load data from Excel file
df = pd.read_excel(file_path)
texts, labels = load_data_from_excel(df, text_column, label_column)

# Split the data
data = pd.DataFrame({text_column: texts, label_column: labels})
train_data, test_data = train_test_split(data, test_size=0.2, random_state=42)
val_data, test_data = train_test_split(test_data, test_size=0.5, random_state=42)

print(f'Train data shape: {train_data.shape}')
print(f'Val data shape: {val_data.shape}')
print(f'Test data shape: {test_data.shape}')

# Save test data to Excel
test_data.to_excel(f'{drive_folder_to_save}/test_data.xlsx', index=False)
print(f'{drive_folder_to_save}/test_data.xlsx saved!')

def start_train(df, model_name, batch_size, lr, max_length, num_epochs):

    # Prepare labels
    label_encoder = LabelEncoder()
    labels = df[label_column]
    labels = label_encoder.fit_transform(labels)
    num_labels = len(set(labels))

    # Hugging Face Datasets format
    train_dataset = Dataset.from_pandas(train_data)
    val_dataset = Dataset.from_pandas(val_data)
    test_dataset = Dataset.from_pandas(test_data)

    # Load tokenizer
    tokenizer = AutoTokenizer.from_pretrained(model_name)

    # Tokenize
    train_dataset = train_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=train_dataset.column_names)
    val_dataset = val_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=val_dataset.column_names)
    test_dataset = test_dataset.map(lambda x: tokenize_dataset(x, tokenizer, max_length, num_labels), batched=True, remove_columns=test_dataset.column_names)

    # Load model
    model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=num_labels, problem_type="multi_label_classification")

    # Training arguments
    training_args = TrainingArguments(
        output_dir=drive_folder_to_save,
        logging_dir=drive_folder_to_save,
        logging_strategy='epoch',
        logging_steps=100,
        num_train_epochs=num_epochs,
        per_device_train_batch_size=batch_size,
        per_device_eval_batch_size=batch_size,
        learning_rate=lr,
        seed=42,
        save_strategy='epoch',
        save_steps=100,
        evaluation_strategy='epoch',
        eval_steps=100,
        save_total_limit=1,
        load_best_model_at_end=True,
    )

    # Create trainer
    trainer = Trainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=val_dataset,
        compute_metrics=compute_metrics,
        callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
    )

    # Train model
    trainer.train()

    # Evaluate results
    predictions = trainer.predict(test_dataset).predictions
    preds = np.argmax(predictions, axis=1)
    accuracy = accuracy_score(test_data[label_column], preds)
    print(f'Accuracy: {accuracy}')
    precision, recall, f1, _ = precision_recall_fscore_support(test_data[label_column], preds, average='weighted')
    print(f'Precision: {precision}')
    print(f'Recall: {recall}')
    print(f'F1 Score: {f1}')

    # Save model
    trainer.save_model(drive_folder_to_save)

# Define training parameters
model_name = 'xlm-roberta-base'
batch_size = 16
learning_rate = 5e-6
max_length = 128
num_epochs = 10

# Start training
start_train(df, model_name, batch_size, learning_rate, max_length, num_epochs)


Note: you may need to restart the kernel to use updated packages.
Train data shape: (186137, 2)
Val data shape: (23267, 2)
Test data shape: (23268, 2)
/project/home/p_babro/p_babel/v4_slant/test_data.xlsx saved!


Map:   0%|          | 0/186137 [00:00<?, ? examples/s]

Map:   0%|          | 0/23267 [00:00<?, ? examples/s]

Map:   0%|          | 0/23268 [00:00<?, ? examples/s]

Some weights of XLMRobertaForSequenceClassification were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/home/p_babro/miniconda3/lib/python3.12/site-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


Accuracy: 0.8367715317173801
Precision: 0.8369187930273877
Recall: 0.8367715317173801
F1 Score: 0.8360611942926541


In [12]:
# Install necessary libraries
%pip install transformers huggingface_hub python-dotenv

# Import necessary libraries
from transformers import AutoTokenizer
from huggingface_hub import HfApi
import os
from dotenv import load_dotenv

# Load environment variables from .env file
load_dotenv()

# Retrieve the token from the environment variable
hf_token = os.getenv("HF_TOKEN")
if not hf_token:
    raise ValueError("Please set the HF_TOKEN environment variable.")

# Define your save directory and Hugging Face repository information
drive_folder_to_save = '/project/home/p_babro/p_babel/v4_slant'
repo_id = "ringorsolya/Emotion_RoBERTa_pooled_V4"

# Set environment variable to avoid the parallelism warning
os.environ["TOKENIZERS_PARALLELISM"] = "false"

# Initialize the HfApi with your token
api = HfApi()

# Ensure the folder exists and contains files
if os.path.exists(drive_folder_to_save) and os.listdir(drive_folder_to_save):
    print(f"Uploading folder {drive_folder_to_save} to Hugging Face repository {repo_id}")
    
    # Upload the model folder to the Hugging Face repository
    api.upload_folder(
        folder_path=drive_folder_to_save,
        repo_id=repo_id,
        token=hf_token
    )
    
    print("Folder upload completed.")
else:
    print(f"The folder {drive_folder_to_save} does not exist or is empty.")

# Load the tokenizer (use the correct model name if different)
tokenizer = AutoTokenizer.from_pretrained("xlm-roberta-base")  # Or the name of your saved model

# Push the tokenizer to the Hugging Face repository
tokenizer.push_to_hub(
    repo_id=repo_id,
    use_auth_token=hf_token
)

print("Tokenizer upload completed.")


Note: you may need to restart the kernel to use updated packages.


ValueError: Please set the HF_TOKEN environment variable.